In [ ]:
!pip install simpletransformers
!pip install wandb
!pip install gradio
!pip install typing-extensions==3.10.0.0

  Using cached typing_extensions-4.9.0-py3-none-any.whl (32 kB)
  Attempting uninstall: typing-extensions
    Found existing installation: typing-extensions 3.10.0.0
    Uninstalling typing-extensions-3.10.0.0:
      Successfully uninstalled typing-extensions-3.10.0.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
lida 0.0.10 requires kaleido, which is not installed.
tensorflow-probability 0.22.0 requires typing-extensions<4.6.0, but you have typing-extensions 4.9.0 which is incompatible.


In [ ]:
import json
import logging
from simpletransformers.question_answering import QuestionAnsweringModel, QuestionAnsweringArgs

In [ ]:
model_type = "bert"
model_name = "bert-base-cased"

In [ ]:
with open(r"/content/test.json", "r") as read_file:
    test = json.load(read_file)

In [ ]:
with open("/content/konbert-export-a07a2fb8c3174.json", "r") as json_file:
    train_data = json.load(json_file)


adapted_data = []
for paragraph in train_data:
    qas_list = []
    if "answers" in paragraph and "text" in paragraph["answers"] and "answer_start" in paragraph["answers"]:
        for i in range(len(paragraph["answers"]["text"])):
            answer_text = paragraph["answers"]["text"][i].strip()
            if answer_text:
                qa_dict = {
                    "id": f"{paragraph['id']}_{i}",
                    "question": paragraph.get("question", ""),
                    "answers": [{"text": answer_text, "answer_start": paragraph["answers"]["answer_start"][i]}]
                }
                qas_list.append(qa_dict)

        if qas_list:
            adapted_data.append({
                "context": paragraph.get("context", ""),
                "qas": qas_list
            })

In [ ]:

model_args = QuestionAnsweringArgs()
model_args.train_batch_size = 16
model_args.evaluate_during_training = True
model_args.n_best_size = 3
model_args.num_train_epochs = 5

train_args = {
    "reprocess_input_data": True,
    "overwrite_output_dir": True,
    "use_cached_eval_features": True,
    "output_dir": "/content/models/bert-base-uncased",  # Specify the directory to save the model
    "best_model_dir": "/content/models/bert-base-uncased/best_model",
    "evaluate_during_training": True,
    "max_seq_length": 128,
    "num_train_epochs": 5,
    "evaluate_during_training_steps": 1000,
    "wandb_project": "Question Answer Application",
    "wandb_kwargs": {"name": model_name},
    "save_model_every_epoch": False,
    "save_eval_checkpoints": False,
    "n_best_size": 3,
    "train_batch_size": 128,
    "eval_batch_size": 64,
}


model = QuestionAnsweringModel('bert', 'bert-base-uncased', args={'overwrite_output_dir': True, 'num_train_epochs': 20})
model.train_model(adapted_data, num_train_epochs=20)
model.save_model(f"outputs/{model_type}/final_model")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
Some weights of BertForQuestionAnswering were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['qa_outputs.bias', 'qa_outputs.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
add example index and unique id: 100%|██████████| 38/38 [00:00<00:00, 254200.24it/s]


Epoch:   0%|          | 0/20 [00:00<?, ?it/s]

Running Epoch 0 of 20:   0%|          | 0/5 [00:00<?, ?it/s]

Running Epoch 1 of 20:   0%|          | 0/5 [00:00<?, ?it/s]

Running Epoch 2 of 20:   0%|          | 0/5 [00:00<?, ?it/s]

...

Running Epoch 15 of 20:   0%|          | 0/5 [00:00<?, ?it/s]

Running Epoch 16 of 20:   0%|          | 0/5 [00:00<?, ?it/s]

Running Epoch 17 of 20:   0%|          | 0/5 [00:00<?, ?it/s]

Running Epoch 18 of 20:   0%|          | 0/5 [00:00<?, ?it/s]

Running Epoch 19 of 20:   0%|          | 0/5 [00:00<?, ?it/s]

In [ ]:
result, texts = model.eval_model(test)

add example index and unique id: 100%|██████████| 3/3 [00:00<00:00, 41527.76it/s]


Running Evaluation:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
to_predict = [
    {
        "context" : "The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10th and 11th centuries gave their name to Normandy, a region in France. They were descended from Norse (\"Norman\" comes from \"Norseman\") raiders and pirates from Denmark, Iceland and Norway who, under their leader Rollo, agreed to swear fealty to King Charles III of West Francia. Through generations of assimilation and mixing with the native Frankish and Roman-Gaulish populations, their descendants would gradually merge with the Carolingian-based cultures of West Francia. The distinct cultural and ethnic identity of the Normans emerged initially in the first half of the 10th century, and it continued to evolve over the succeeding centuries.",
        "qas": [
            {
                "question": "Who were the Normans?",
                "id": "56ddde6b9a695914005b9628",
            }
        ],
    }
]

In [ ]:
answers, probabilities = model.predict(to_predict)
top_answer = answers[0]['answer'][0]
print(top_answer)

add example index and unique id: 100%|██████████| 1/1 [00:00<00:00, 12264.05it/s]


Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

10th and 11th centuries


In [ ]:
"""model = QuestionAnsweringModel('bert', '/content/outputs', args={'overwrite_output_dir': True})

def chatbot():
    while True:
        question = input("Enter question: ")

        if question.lower() == 'exit':
            print("Chatbot: Goodbye!")
            break

        to_predict = [
            {
                "context": "The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10th and 11th centuries gave their name to Normandy, a region in France. They were descended from Norse (\"Norman\" comes from \"Norseman\") raiders and pirates from Denmark, Iceland and Norway who, under their leader Rollo, agreed to swear fealty to King Charles III of West Francia. Through generations of assimilation and mixing with the native Frankish and Roman-Gaulish populations, their descendants would gradually merge with the Carolingian-based cultures of West Francia. The distinct cultural and ethnic identity of the Normans emerged initially in the first half of the 10th century, and it continued to evolve over the succeeding centuries.",
                "qas": [
                    {
                        "question": question,
                        "id": "user_question",
                    }
                ],
            }
        ]

        answers, probabilities = model.predict(to_predict)

        top_answer = answers[0]['answer'][0]
        print(f"Chatbot: {top_answer}")

chatbot()"""


Enter question: exit
Chatbot: Goodbye!


In [ ]:
"""import gradio as gr

def chatbot(question):
    to_predict = [
        {
            "context": "The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10th and 11th centuries gave their name to Normandy, a region in France. They were descended from Norse (\"Norman\" comes from \"Norseman\") raiders and pirates from Denmark, Iceland and Norway who, under their leader Rollo, agreed to swear fealty to King Charles III of West Francia. Through generations of assimilation and mixing with the native Frankish and Roman-Gaulish populations, their descendants would gradually merge with the Carolingian-based cultures of West Francia. The distinct cultural and ethnic identity of the Normans emerged initially in the first half of the 10th century, and it continued to evolve over the succeeding centuries.",
            "qas": [
                {
                    "question": question,
                    "id": "user_question",
                }
            ],
        }
    ]

    answers, probabilities = model.predict(to_predict)
    top_answer = answers[0]['answer'][0]
    return top_answer

iface = gr.Interface(
    fn=chatbot,
    inputs="text",
    outputs="text",
    live=True,
    title="Chatbot Interface",
    description="Ask a question about the Normans",
)

iface.launch()"""


Setting queue=True in a Colab notebook requires sharing enabled. Setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
Running on public URL: https://90c3a30cfad25a2284.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)
